In [2]:
original_seq = ['a','b','c','d','e','f']
min_len = 1
max_len = 3


contig_seqs = list()

for st in range(len(original_seq)):
    min_fin_index = st + min_len
    max_fin_index = min(st + max_len, len(original_seq)) + 1

    for fin in range(min_fin_index, max_fin_index):
        seq = original_seq[st:fin]
        contig_seqs.append(seq)

for cs in contig_seqs:
    print(''.join(cs))


a
ab
abc
b
bc
bcd
c
cd
cde
d
de
def
e
ef
f


In [ ]:
from scipy import stats
import heapq # to extract n largest values with nlargest()

# PARAMS

seq = ['a','b','c','d','e','f','e'] # trials
N = 2 # N as in N-Back


trials = len(seq)

def count_targets_and_lures():
    # the first trials are distractors
    mask = 'D' * N
    for index in range(N, trials):
        if seq[index] == seq[index - N]:
            mask += 'T'
        elif seq[index] in seq[index - N - 1:index - N + 1]:
            mask += 'L'
        else:
            mask += 'D'
    return mask.count('T'), mask.count('L')


targets,lures = count_targets_and_lures()
targets_norm = stats.norm(targets, 0.5)
skewness_norm = stats.norm(0, 0.5)

def skewness_cost(choices):
    even_ratio = len(seq) / len(choices)
    costs = {c: abs(seq.count(c) - even_ratio) for c in choices}
    max_deviation_from_even_dist = max(list(costs.values()))
    cost = 1.0 - (skewness_norm.pdf(max_deviation_from_even_dist) / skewness_norm.pdf(0))
    return cost



def lures_ratio_cost():
    return 1.0 - targets_norm.pdf(targets)


def targets_ratio_cost():
    return 1.0 - targets_norm.pdf(targets)

def ralph2014_skewness(choices):
    freqs = [float(seq.count(c)) for c in choices]
    ralph_skewed = sum(heapq.nlargest(int(len(choices) / 2), freqs)) > (trials * 2 / 3)
    return ralph_skewed